In [12]:
options(readr.num_columns = 0)
library(robservable)
library(tidyverse)
library(readxl)
library(lubridate)
library(geosphere)
library(plotly)
library(highcharter)
library(gganimate)
library(shiny)
library(shinythemes)
library(shinydashboard)
library(leaflet)
library(RColorBrewer)
library(formattable)


# **Inputs**

In [17]:
input_demand <- 200
input_legume <- "carrot"
input_code <- 1348
input_time <- "december"
input_production_mode <- "organic"
input_transformation <- "processed"

# **Get Province**

In [75]:
GetProvince = function(input_code){
    file = 'Database projet.xlsx'
    provinces = read_excel(file, sheet = 'provinces')
    file = 'code-postaux-belge.csv'
    df = read_csv2(file)
    province_vector = vector()
    distances = vector()
    names = vector()
    test = df%>%filter(Code == input_code)
    
    if(length(test$Code) == 0){return(numeric(0))}

    lon1 = (df%>%filter(Code == input_code))$Longitude[[1]]

    lat1 = (df%>%filter(Code == input_code))$Latitude[[1]]
    localite = (df%>%filter(Code == input_code))$Localite

    for (i in seq(from = 1, to = nrow(provinces), by = 1)){
    prov = provinces[i,][['id_province']]
    lon2 = provinces[i,][['longitude']]
    lat2 = provinces[i,][['latitude']]
    name = provinces[i,][['name']]
    dist = distm(c(lon1, lat1), c(lon2, lat2), fun = distHaversine)

    province_vector = append(province_vector, prov)
    distances = append(distances, dist)  
    names = append(names, name)
    }
    df = data.frame()
    df = cbind(data.frame(province_vector), data.frame(distances), data.frame(names))
    df = df[order(df$distances),]
    output_list = list(df, localite)
    return(output_list)
    }

# **Get Production**

In [76]:
get_production <- function(input_product_id, input_province_id, yealds_id){
  
  # look to the purcentage of surface attributed to the product
  # ex : there is 75% of the carrot surface attributed to the reasoned conventionnal agric.
  specific_purcent <- (repartition_modes %>% filter(id_product == input_product_id))$"%"
  
  # look for the legume of the product
  legume <- (repartition_modes %>% filter(id_product == input_product_id))$id_legume
  
  # calculate the surface 
  specific_surface <- specific_purcent*(surfaces %>% filter(id_legume == legume,
                                           id_province == input_province_id))$surface
  
  
  # look to the specific yield of the product (in T/ha)

  specific_yield <- (production_impacts %>% filter(id_product == input_product_id,
                                                  id_impact == yealds_id))$value
  

  # Calculate the production
  specific_production <- specific_surface*specific_yield

  return(specific_production)
}

# Get Production

In [79]:
#==============================
# GET PRODUCTION BASIC FUNCTION
#==============================

get_production <- function(input_product_id, input_localisation, yealds_id){
  #=============================================================
  # Return the production of a given product in a given province
  #=============================================================
  
  # look to the purcentage of surface attributed to the product
  # ex : there is 75% of the carrot surface attributed to the reasoned conventionnal agric.
  specific_purcent <- (repartition_modes %>% filter(id_product == input_product_id))$"%"
  
  # look for the legume of the product
  legume <- (products %>% filter(id_product == input_product_id))$id_legume
  
  # calculate the surface 
  specific_surface <- specific_purcent*(surfaces %>% filter(id_legume == legume,
                                           id_province == input_localisation))$surface
  
  
  # look to the specific yield of the product (in T/ha)
  specific_yield <- (production_impacts %>% filter(id_product == input_product_id,
                                                  id_impact == yealds_id))$value
  
  # Calculate the production
  specific_production <- (specific_surface*specific_yield)

  return(specific_production)
}


#==============================
# GET PRODUCTION FRESH
#==============================

get_production_fresh <- function(input_product_id, yealds_id, input_demand, province_order, harvest_time, conservation_time){
  
  temp_province_order <- 1  # take the value of the province during the iteration
  end = FALSE               # if end is true, while loop ends
  total_offer <- 0          # total_offer initialization
  status <- NULL
  
  list_production <- data.frame(province = c(),
                                production = c(),
                                status = c())
  
  while(end == FALSE){
    input_localisation <- province_order[temp_province_order,1]
    input_localisation_name = (provinces %>% filter(id_province == input_localisation))$name
    
    offer <- get_production(input_product_id,
                            input_localisation,
                            yealds_id)
    offer <- offer/(length(harvest_time)+length(conservation_time))
    total_offer <- total_offer + offer
    
    if(total_offer >= input_demand)
    {
    #output_list = list(input_localisation_name, total_offer, input_demand)
    #print(paste0("There is enough in ", input_localisation_name, ". Current offer is ",total_offer,"t while the demand is ",input_demand,"t."))
    status <- paste0("There is enough in ", input_localisation_name)
    status_id = 1
    
    end = TRUE
    
    }
    
    else
    {
      if (temp_province_order >= length(province_order[,1]))
      {
        end = TRUE
        
        status <- "There is not enough production in Wallonia for your request."
        status_id = 0
      }
      else
      {
        #print(paste0("There is not enough in ", input_localisation_name,", let's search in neighboring provinces."))
        #print(paste0("demand : ", input_demand, " | total offer : ",total_offer))
        status <- paste0("There is not enough in ", input_localisation_name)
        status_id = 0
      
      }
      
      temp_province_order <- temp_province_order + 1
    }
    
    #==========================
    # Encodage & sauvegarde
    #==========================
    
    temp <- data.frame(name = input_localisation_name,
                       production = offer,
                       status = status,
                       status_id)
    
    list_production <- rbind(list_production, temp)
    
  }
  return(list_production)
}



#==============================
# GET PRODUCTION TRANSFORMED
#==============================

get_production_transform <- function(input_product_id, yealds_id, input_demand, province_order){
  
  temp_province_order <- 1  # take the value of the province during the iteration
  temp_status <- NULL
  end = FALSE               # if end is true, while loop ends
  total_offer <- 0          # total_offer initialization
  
  list_production <- data.frame(province = c(),
                                production = c(),
                                status = c())
  
  while(end == FALSE){
    input_localisation <- province_order[temp_province_order,1]
    input_localisation_name = (provinces %>% filter(id_province == input_localisation))$name
    #print(paste0("Searching in ", input_localisation_name))
    
    offer <- get_production(input_product_id,
                            input_localisation,
                            yealds_id)
    offer <- offer/12
    total_offer <- total_offer + offer
    
    if(total_offer > input_demand)
    {
      end = TRUE
      output_list = list(input_localisation_name, total_offer, input_demand)
      
      
      #print(paste0("There is enough in ", input_localisation_name, ". Current offer is ",total_offer,"t while the demand is ",input_demand,"t."))
      
      status <- paste0("There is enough in ", input_localisation_name)
        status_id = 1
      
    }
    
    else
    {
      if (temp_province_order >= length(province_order[,1]))
      {
        end = TRUE
        #print("There is not enough production in Wallonia for your request.")
        status <- "There is not enough production in Wallonia for your request."
          status_id = 0
        
        
      }
      else
      {
        #print(paste0("There is not enough in ", input_localisation_name,", let's search in neighboring provinces."))
        status <- paste0("There is not enough in ", input_localisation_name)
          status_id = 0
        
      }
      
      
      
      temp_province_order <- temp_province_order + 1
    }
    
    #==========================
    # Encodage & sauvegarde
    #==========================
    
    temp <- data.frame(name = input_localisation_name,
                       production = offer,
                       status = status,
                       status_id)
    
    list_production <- rbind(list_production, temp)
    
  }
  return(list_production)
}

# **Get Impacts**

In [80]:
get_impacts <-
  function(input_product_id,
           production) 
    {
    # TEST
    #input_product_id = 15
    #production = 200
    
    
    
    id_surface = (impacts %>% filter(name == "Surface de terre"))$id_impact
    
    # calculate the surface
    specific_surface <-
      production * ((
        production_impacts %>% filter(id_product == input_product_id,
                                      id_impact == id_surface)
      )$value) 
    # dans la DB, la surface par qtt est en ha*10-3 par kilo. 
    # En multipliant par la demande en tonnes, 
    # on obtient directement la surface spécifique en ha
    
    print(paste0("Specific surface : ",specific_surface," ha"))
    
    list_impact = data.frame(name = c(),
                             value = c(),
                             units = c(),
                             incertitude = c()
                             )
    
    for (impact_id in c(1:length(impacts$id_impact))) {                              # !!!! si les id changent (pas très optimal mais j'ai pas réussi à transformer une colonne de df en liste)
      
      #===========================================
      # EXCEPTION SI IMPACT + RENDEMENT OU SURFACE
      #===========================================
      
      #if(impact_id == (impacts %>% filter(name == "Surface de terre"))$id_impact){
        # do nothing
      #}
      
      if(impact_id == (impacts %>% filter(name == "Rendements"))$id_impact){
        # do nothing
      }
      
      #===========================================
      # CALCUL DES IMPACTS
      #===========================================
      
      else{
      #print(impact_id)
      impact_value_final <- 0
      
      # NAME
      impact_name <- (impacts %>% filter(id_impact == impact_id))$name
      
      # UNITS
      impact_units1 <-
        (impacts %>% filter(id_impact == impact_id))$units1
      
      impact_units2 <-
        (impacts %>% filter(id_impact == impact_id))$units2
      
      # VALUE
      impact_value <-
        (
          production_impacts %>% filter(id_impact == impact_id,
                                        id_product == input_product_id)
        )$value
      
      #=============================================
      # 1. Cas ou l'impact est en unité par kilo
      
      if (impact_units2 == "kg")
      {
        impact_value_final <- impact_value * production * 1000 #multiply by 1000 because production is in t
      }
      
      #=============================================
      # 2. Cas ou l'impact est en unité par hectare
      
      else if (impact_units2 == "ha")
      {
        impact_value_final <- impact_value * specific_surface
      }
      
      #=============================================
      # 3. Cas ou l'impact est en unité par kilo par jour
      else if (impact_units2 == "kg.jour")  # cas du stockage
      {
        impact_value_final <- 0.00122 * production * 1000                       # Valeur rentrée mannuellement. Automatiser?
      }
      
      #=============================================
      # EXCEPTIONS
      #=============================================
      else{
        if (impact_name == "DQR"){
          DQR_id <- (impacts %>% filter(name == "DQR"))$id_impact
          impact_value_final = (production_impacts %>% filter(id_product == input_product_id,
                                                              id_impact == DQR_id))$value
        }
        
        else{print(paste0("Error : impact not found. Impact ID is : ",impact_id))}
      }
      
      #=============================================
      # Encodage et sauvegarde
      #=============================================
      temp <- data.frame(name = impact_name,
                         value = impact_value_final,
                         units = impact_units1,
                         incertitude = (impacts %>% filter(name == impact_name))$incertitude)
      list_impact <- rbind(list_impact, temp)
      
      #print(paste0("The impact on ",impact_name," is ",impact_value_final," ",impact_units1))
      
      }
      
    }
  return(list_impact)
  }


# **Data Definition**

In [81]:
########################################
# Variable definitions
########################################

# 1 - Model variables
# these are the variables we would like to estimate with the model

production_locations <- NULL
production_total <- NULL
environmental_impact <- NULL
production_times <- NULL


# 2 - Data tables
# These are the tables loaded from the database
surfaces <- NULL
provinces <- NULL
legumes <- NULL
production_modes <- NULL
transformation <- NULL
repartition_modes <- NULL
impacts <- NULL
production_impacts <- NULL

# 3 - Other variables
months <- c("january", "february", "march", "april", "may", "june", "july", "august", "september", "october", "november", "december")

########################################
# Load the database tables
########################################

#Pathway : copy & paste here the database pathway
pathway = "Database projet.xlsx"

surfaces <- read_xlsx(pathway, sheet="surfaces")
provinces <- read_xlsx(pathway, sheet="provinces")
legumes <- read_xlsx(pathway, sheet="legumes")
production_modes <- read_xlsx(pathway, sheet="production_modes")
transformation <- read_xlsx(pathway, sheet="transformation")
repartition_modes <- read_xlsx(pathway, sheet="%_modes")
prices <- read_xlsx(pathway, sheet="prices")
impacts <- read_xlsx(pathway, sheet="impacts")
production_impacts <- read_xlsx(pathway, sheet="production_impacts")
products <- read_xlsx(pathway, sheet="Product")


########################################
# Process the datatables
########################################

# impact_data <- merge(production_impacts, impacts, by.x = "id_impact", by.y = "id_impact") %>%  
#   select(-name)
impact_data <- merge(production_impacts, impacts, by.x = "id_impact", by.y = "id_impact")
impact_data <- merge(impact_data, products, by.x = "id_product",by.y = "id_product")


# Get Production Province

In [82]:
get_production_province <- function(input_product_id, input_time, input_province_id){
  
  input_production_mode_id <- (products %>% filter(id_product == input_product_id))$id_mode
  input_production_mode <- (production_modes %>% filter(id_mode == input_production_mode_id))$name
  
  input_transformation_id <- (products %>% filter(id_product == input_product_id))$id_transformation
  input_transformation <- (transformation %>% filter(id_transformation == input_transformation_id))$transformation
  
  months <- c("january", "february", "march", "april", "may", "june", "july", "august", "september", "october", "november", "december")
  input_legume_id <- (products %>% filter(id_product == input_product_id))$id_legume
  input_time_id <- which(months == input_time)
  
  # harvest
  harvest_start <- (legumes %>% filter(id_legume == input_legume_id))$"harvest start"
  harvest_stop <- (legumes %>% filter(id_legume == input_legume_id))$"harvest stop"
  if (harvest_stop < harvest_start){
    harvest_time <- seq(harvest_start,12,by=1)
    harvest_time <- c(harvest_stop,seq(1,harvest_stop,by=1))
  }else{harvest_time <- seq(harvest_start,harvest_stop,by=1)}
  
  # conservation
  conservation_start <- (legumes %>% filter(id_legume == input_legume_id))$"conservation start"
  conservation_stop <- (legumes %>% filter(id_legume == input_legume_id))$"conservation stop"
  if (conservation_stop < conservation_start){
    conservation_time <- seq(conservation_start,12,by=1)
    conservation_time <- c(conservation_time,seq(1,conservation_stop,by=1))
  }else{conservation_time <- seq(conservation_start,conservation_stop,by=1)}
  
  if(input_transformation_id == 1){
    
    legume_id <- (products %>% filter(id_product == input_product_id))$id_legume
    legume <- (legumes %>% filter(id_legume == legume_id))$name
    demand = 100000000000000000
    variable <- Main(demand, legume, input_code, input_time, input_production_mode, input_transformation)
    variable <- variable[[1]]
    
    province <- (provinces %>% filter(id_province == input_province_id))$name
    variable <- (variable %>% filter(name == province))$production
  }
    
  else if (input_transformation_id == 2){
  
    if(input_time_id %in% harvest_time){
      legume_id <- (products %>% filter(id_product == input_product_id))$id_legume
      legume <- (legumes %>% filter(id_legume == legume_id))$name
      demand = 100000000000000000
      variable <- Main(demand, legume, input_code, input_time, input_production_mode, input_transformation)
      variable <- variable[[1]]
      
      province <- (provinces %>% filter(id_province == input_province_id))$name
      variable <- (variable %>% filter(name == province))$production
    }
    
    else if(input_time_id %in% conservation_time){
      legume_id <- (products %>% filter(id_product == input_product_id))$id_legume
      legume <- (legumes %>% filter(id_legume == legume_id))$name
      demand = 100000000000000000
      variable <- Main(demand, legume, input_code, input_time, input_production_mode, input_transformation)
      variable <- variable[[1]]
      
      province <- (provinces %>% filter(id_province == input_province_id))$name
      variable <- (variable %>% filter(name == province))$production
    }
    
    else{
      variable <-0
    }
  }
    
  else{
    variable <- NULL
  }
  
  return(variable)
}

# Get Means

In [86]:
Get_Means = function(){

  #============================
  # MODES
  #============================
  
  impact_means <- data.frame(id_impact = c(), 
                             id_mode = c(), 
                             mean = c())
  
  for (j in impacts[1:14,]$id_impact){  # car dans impact il y a aussi le stockage
     
    # print("==================")
    # print((impacts %>% filter(id_impact==j))$name)
    # print("==================")
    
    temp_means_vec = NULL
    
    
    # pour chaque impact
    for (i in production_modes$id_mode){ 
      
      temp = NULL
      
      # print((production_modes %>% filter(id_mode == i))$name)
      
      # calcule la moyenne
      
      temp_means = mean((impact_data %>% filter(id_mode == i,
                                               id_impact == j))$value)
      
      temp = data.frame(id_impact = j, 
                        id_mode = i, 
                        mean = temp_means)
      
      temp_means_vec = rbind(temp_means_vec, temp)
      
    }
    
    impact_means = rbind(impact_means,temp_means_vec)
    
  }
  
  #print(impact_means)
  
  #============================
  # TRANSFORMATIONS
  #============================
  
  impact_means2 <- data.frame(id_impact = c(), 
                             id_transformation = c(), 
                             mean = c())
  
  for (j in impacts[1:14,]$id_impact){  # car dans impact il y a aussi le stockage
    
    # print("==================")
    # print((impacts %>% filter(id_impact==j))$name)
    # print("==================")
    
    temp_means_vec = NULL
    
    
    # pour chaque impact
    for (i in transformation$id_transformation){ 
      
      temp = NULL
      
      # print((production_modes %>% filter(id_mode == i))$name)
      
      # calcule la moyenne
      
      temp_means = mean((impact_data %>% filter(id_transformation == i,
                                                id_impact == j))$value)
      
      temp = data.frame(id_impact = j, 
                        id_transformation = i, 
                        mean = temp_means)
      
      temp_means_vec = rbind(temp_means_vec, temp)
      
    }
    
    impact_means2 = rbind(impact_means2,temp_means_vec)
    
  }
  
  #print(impact_means2)
  
  return(list(impact_means,impact_means2))
}

# Main 2

In [83]:
########################################
# Load the libraries, functions & datas
########################################
# rm(list=ls())                                                                   # Clean all variables
# setwd(dirname(rstudioapi::getActiveDocumentContext()$path))                     # Set working directory to the current file
# pathway = "Database projet.xlsx"                                                # link the database

library(tidyverse)
library(readxl)
library(lubridate)
library(geosphere)
library(data.table)


#source("Data definition.R")
# source("Get_Production.R")
# source("Get_Province.R")
# #source("Get_Production_Monthly.R")
# source("Inputs.R")
# source("Get_Impacts.R")


Main = function(input_demand, input_legume, input_code, input_time, input_production_mode, input_transformation){
  #==========================
  # 1. GET THE IDs
  #==========================
  # yealds :
  yealds_id <- (impacts %>% filter(name == "Rendements"))$id_impact
  
  # legumes
  input_legume_id <- (legumes%>% filter(name == input_legume))$id_legume
  
  # production modes
  input_production_mode_id <- (production_modes %>% filter(name == input_production_mode))$id_mode
  
  # transformations
  input_transformation_id <- (transformation %>% filter(transformation == input_transformation))$id_transformation
  
  # product
    
  input_product_id <- (products %>% filter(
                                id_mode == input_production_mode_id,
                                id_transformation == input_transformation_id,
                                id_legume == input_legume_id))$id_product
  
  input_time_id <- which(months == input_time)
  #==========================
  # 2. GET THE TIMES
  #==========================
  # Some manipulation needed if for ex time start in november (11) and ends in february (2) -> length = (12-11) + 2
  
  # harvest
  harvest_start <- (legumes %>% filter(id_legume == input_legume_id))$"harvest start"
  harvest_stop <- (legumes %>% filter(id_legume == input_legume_id))$"harvest stop"
  if (harvest_stop < harvest_start){
    harvest_time <- seq(harvest_start,12,by=1)
    harvest_time <- c(harvest_stop,seq(1,harvest_stop,by=1))
  }else{harvest_time <- seq(harvest_start,harvest_stop,by=1)}
  
  # conservation
  conservation_start <- (legumes %>% filter(id_legume == input_legume_id))$"conservation start"
  conservation_stop <- (legumes %>% filter(id_legume == input_legume_id))$"conservation stop"
  if (conservation_stop < conservation_start){
    conservation_time <- seq(conservation_start,12,by=1)
    conservation_time <- c(conservation_time,seq(1,conservation_stop,by=1))
  }else{conservation_time <- seq(conservation_start,conservation_stop,by=1)}
  
  #==========================
  # 3. PREPARATION
  #==========================
  
  # Errors
  if(length(input_product_id) == 0){return("No data :(")}
  test = GetProvince(input_code)
  if(length(test) == 0){return("Enter a valid postal code")}
  
  province_order <- GetProvince(input_code)[[1]] # Get the order of the provinces
  Our_location = GetProvince(input_code)[[2]]    # Name of the localization (ex : "Louvain-la-Neuve")

  # various
  temp_province_order <- 1  # take the value of the province during the iteration
  end = FALSE               # if end is true, while loop ends
  total_offer <- 0          # total_offer initialization
  status <- NULL            # will save the status of the production
  status_id <- NULL
  
  #input_localisation <- province_order[temp_province_order,1]
  #input_localisation_name = (provinces %>% filter(id_province == input_localisation))$name
  
  # Request recap :
  #print(paste0("Resquest recap ; searching for ", input_demand, 
  #             " t of ", input_production_mode,
  #             " ", input_transformation,
  #             " ", input_legume, 
  #             " in ", province_order[1,3], 
  #             " in ", input_time))
    
  #===================
  # 4. GET THE PRODUCTION
  #===================
    
  # 1. Case of transformed product : get monthly production
  if (input_transformation_id == 1){ 
    offer <- get_production_transform(input_product_id,
                                      yealds_id, 
                                      input_demand, 
                                      province_order)
  }
    
  # 2. Case of fresh product : divide production by harvest and conservation time
  else if (input_transformation_id == 2){
    
    # 2.1 It is the season
    if(input_time_id %in% harvest_time){
      #print("It is still the season.")                                 
      status <- "It is still the season."
      offer <- get_production_fresh(input_product_id, 
                                    yealds_id, 
                                    input_demand, 
                                    province_order,
                                    harvest_time,
                                    conservation_time)
    
    # 2.2 Not hte season but stocks
    }else if (input_time_id %in% conservation_time){ 
      #print("It is not the season anymore but there is conservation stocks.")
      status <- "It is not the season anymore but there is conservation stocks."
      offer <- get_production_fresh(input_product_id, 
                                    yealds_id, 
                                    input_demand, 
                                    province_order,
                                    harvest_time,
                                    conservation_time)
    
    # 2.3 Not the season and no stocks
    }else{
      #print("It is not the season anymore and there is no more conserved stocks.")}
      status <- "It is not the season anymore and there is no more conserved stocks."
      output = list(data.frame(paste(status)), data.frame(paste("No impact to show")))
          return(output)
    }
      }
      

  
  # 3. Outputs
    impact_final <- get_impacts(input_product_id,input_demand)
    output <- list(offer, impact_final)
  return(output)
  
}

# test <- Main(input_demand, input_legume, input_code, input_time, input_production_mode, input_transformation)
# pour acceder à l'offre : test[[1]]
# pour acceder aux impacts : test[[2]]

In [84]:
input_demand <- 200
input_legume <- "pea"
input_code <- 1348
input_time <- "july"
input_production_mode <- "organic"
input_transformation <- "fresh"

df = Main(input_demand, input_legume, input_code, input_time, input_production_mode, input_transformation)
df[[1]]

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.



[1] "Specific surface : 34 ha"


name                       production
1 Province du Brabant wallon 0         
2 Province de Namur          0         
3 Province de Hainaut        0         
4 Province de Liège          0         
5 Province de Luxembourg     0         
  status                                                       status_id
1 There is not enough in Province du Brabant wallon            0        
2 There is not enough in Province de Namur                     0        
3 There is not enough in Province de Hainaut                   0        
4 There is not enough in Province de Liège                     0        
5 There is not enough production in Wallonia for your request. 0

In [85]:
df[[2]]

name                     value    units        incertitude
1  Quantité eau             1.80e+04 m^3 deprived 3.00000    
2  Qte CO2                  7.80e+04 kg CO2       1.00000    
3  Surface de terre         3.40e+04 ha*10-3      1.00000    
4  Energie requise          1.33e+06 MJ           3.00000    
5  Ressource en travail     0.00e+00 Heures       2.00000    
6  Désherbage méca          0.00e+00 #passage     2.00000    
7  PPT Chimiques            0.00e+00 #dose ref    2.00000    
8  PPT Bios                 0.00e+00 #dose ref    2.00000    
9  Couche O3                1.80e+04 CVC11        1.00000    
10 Acidification            0.00e+00 mol H+       2.00000    
11 Eutrophisation terrestre 2.00e+03 mol N        2.00000    
12 Global score             1.80e+04 -                 NA    
13 DQR                      2.43e+00 -                 NA    
14 Stockage                 2.44e+02 kg CO2       0.00122

In [88]:
Get_Means()

[[1]]
   id_impact id_mode         mean
1          1       1  11.99000000
2          1       2   7.62125000
3          1       3   7.62125000
4          1       4   3.25250000
5          2       1   1.64000000
6          2       2   1.03000000
7          2       3   1.03000000
8          2       4   0.42000000
9          3       1   0.06107143
10         3       2   0.06075716
11         3       3   0.07613636
12         3       4   0.08277778
13         4       1 123.68000000
14         4       2  66.14875000
15         4       3  66.14875000
16         4       4   8.61750000
17         5       1   7.00000000
18         5       2  62.87500000
19         5       3 140.00000000
20         5       4 225.00000000
21         6       1   0.00000000
22         6       2   0.37500000
23         6       3   2.00000000
24         6       4   2.00000000
25         7       1   5.87500000
26         7       2   5.31250000
27         7       3   0.00000000
28         7       4   0.00000000
29         8       1   0.00000000
30         8       2   0.00000000
31         8       3   3.43750000
32         8       4   0.75000000
33         9       1  37.37500000
34         9       2  35.62500000
35         9       3  29.75000000
36         9       4  23.75000000
37        10       1   0.58750000
38        10       2   0.33500000
39        10       3   0.33500000
40        10       4   0.08250000
41        11       1   0.01250000
42        11       2   0.00750000
43        11       3   0.00750000
44        11       4   0.00250000
45        12       1   0.03500000
46        12       2   0.02500000
47        12       3   0.02500000
48        12       4   0.01500000
49        13       1   0.20250000
50        13       2   0.29125000
51        13       3   0.29125000
52        13       4   0.38000000
53        14       1   2.77250000
54        14       2   2.55000000
55        14       3   2.55000000
56        14       4   2.32750000

[[2]]
   id_impact id_transformation         mean
1          1                 1  11.99000000
2          1                 2   3.25250000
3          2                 1   1.64000000
4          2                 2   0.42000000
5          3                 1   0.06639610
6          3                 2   0.07281598
7          4                 1 123.68000000
8          4                 2   8.61750000
9          5                 1  27.16666667
10         5                 2 185.41666667
11         6                 1   0.83333333
12         6                 2   1.41666667
13         7                 1   3.33333333
14         7                 2   2.16666667
15         8                 1   0.70833333
16         8                 2   1.83333333
17         9                 1  35.00000000
18         9                 2  28.95833333
19        10                 1   0.58750000
20        10                 2   0.08250000
21        11                 1   0.01250000
22        11                 2   0.00250000
23        12                 1   0.03500000
24        12                 2   0.01500000
25        13                 1   0.20250000
26        13                 2   0.38000000
27        14                 1   2.77250000
28        14                 2   2.32750000

# **Get dispo**

In [28]:
options(warn=-1)

input_demand <- 400
input_legume <- "carrot"
input_code <- 1348
input_time <- "may"
input_production_mode <- "conventionnal"
input_transformation <- "processed"

get_dispo = function(input_demand, input_legume, input_code, input_time, input_production_mode, input_transformation){
    # yealds :
    yealds_id <- (impacts %>% 
                  filter(name == "Rendements")
    )$id_impact

    # legumes
    input_legume_id <- (legumes%>% 
                        filter(name == input_legume)
    )$id_legume

    # production modes
    input_production_mode_id <- (production_modes %>% 
                                 filter(name == input_production_mode)
    )$id_mode

    # transformations
    input_transformation_id <- (transformation %>% 
                                filter(transformation == input_transformation)
    )$id_transformation

    # product
    input_product_id <- (repartition_modes %>% 
                         filter(id_mode == input_production_mode_id,
                                id_transformation == input_transformation_id,
                                id_legume == input_legume_id))$id_product

    production_list = list()
    provinces_id_list = as.numeric(rownames(GetProvince(input_code)[[1]]))
    for(i in provinces_id_list){
        
        production_list = append(production_list, get_production_province(input_product_id, input_time, i))
    }
    
     df = do.call(rbind.data.frame, production_list)
     colnames(df) = "value"
     ndf = cbind(GetProvince(input_code)[[1]], df) 
    
    
    demand_list = vector()
    offer = ndf$value
    for(i in list(1,2,3,4,5)){
        
        
    if(offer[i] >= input_demand){
        
        
        demand_list = append(demand_list, input_demand)
        input_demand = 0
    }
    else{
        demand_list = append(demand_list, offer[i])
        input_demand = input_demand - offer[i]
    }
    }
    
    ndf$demand = demand_list
    print(demand_list)
    return(ndf)
}


In [29]:
ndf = get_dispo(input_demand, input_legume, input_code, input_time, input_production_mode, input_transformation)
ndf

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.

ℹ Using ',' as decimal and '.' as grouping 

[1]  89.25000  92.18533 218.56467   0.00000   0.00000


province_vector distances names                      value     demand   
1 1                4612.102 Province du Brabant wallon  89.25000  89.25000
5 5               29185.678 Province de Namur           92.18533  92.18533
2 2               49009.156 Province de Hainaut        274.61233 218.56467
3 3               85035.254 Province de Liège          172.70867   0.00000
4 4               98473.875 Province de Luxembourg       0.11900   0.00000

In [30]:
df[[2]]

name                     value        units       
1  Quantité eau             6.500000e+05 m^3 deprived
2  Qte CO2                  2.340000e+05 kg CO2      
3  Energie requise          1.029200e+07 MJ          
4  Ressource en travail     5.454545e-01 Heures      
5  Désherbage méca          7.272727e-03 #passage    
6  PPT Chimiques            0.000000e+00 #dose ref   
7  PPT Bios                 2.363636e-02 #dose ref   
8  Couche O3                5.400000e+04 CVC11       
9  Acidification            2.000000e+03 mol H+      
10 Eutrophisation terrestre 4.000000e+03 mol N       
11 Global score             4.400000e+04 -           
12 DQR                      2.890000e+00 -           
13 Stockage                 2.440000e+02 kg CO2

In [31]:
highchart() %>% 
    hc_chart(type = "column") %>%
    hc_xAxis(categories = df[[2]]$name)%>%
    hc_add_series(name="log Impact",
                data = log((df[[2]]$value)),
                 stack = "Values", grouping = TRUE, color = "#FF0BBB",
                  borderColor = "#000000", borderWidth = 3, colorByPoint = TRUE)%>%
          hc_legend(enabled = FALSE)

HTML widgets cannot be represented in plain text (need html)

In [32]:
highchart() %>% 
    hc_chart(type = "column") %>%
    hc_xAxis(categories = ndf$names)%>%
    hc_plotOptions(series = list(clip = TRUE))%>%
    hc_add_series(name="Offer",
                data = ndf$value,
                 stack = "Values", grouping = TRUE, color = "#FF0BBB",
                  borderColor = "#000000", borderWidth = 3)%>%
    hc_add_series(name="Demand",
                data = ndf$demand,
                grouping = FALSE,
                 color = "#ADFF2F",
                 stack = "Values",
                 borderColor = "#000000", borderWidth = 3)
    


HTML widgets cannot be represented in plain text (need html)

In [33]:
df <- data_frame(
  name = c("Animals", "Fruits", "Cars"),
  y = c(5, 2, 4),
  drilldown = tolower(name)
)


ds <- list_parse(df)
names(ds) <- NULL


hc <- highchart() %>%
  hc_chart(type = "column") %>%
  hc_title(text = "Basic drilldown") %>%
  hc_xAxis(type = "category") %>%
  hc_legend(enabled = FALSE) %>%
  hc_plotOptions(
    series = list(
      boderWidth = 0,
      dataLabels = list(enabled = TRUE)
    )
  ) %>%
  hc_add_series(
    name = "Things",
    colorByPoint = TRUE,
    data = ds
  )

dfan <- data_frame(
  name = c("Cats", "Dogs", "Cows", "Sheep", "Pigs"),
  value = c(4, 3, 1, 2, 1)
)

dffru <- data_frame(
  name = c("Apple", "Organes"),
  value = c(4, 2)
)

dfcar <- data_frame(
  name = c("Toyota", "Opel", "Volkswage"),
  value = c(4, 2, 2)
)

second_el_to_numeric <- function(ls){

  map(ls, function(x){
    x[[2]] <- as.numeric(x[[2]])
    x
  })

}

dsan <- second_el_to_numeric(list_parse2(dfan))

dsfru <- second_el_to_numeric(list_parse2(dffru))

dscar <- second_el_to_numeric(list_parse2(dfcar))

hc %>%
  hc_drilldown(
    allowPointDrilldown = TRUE,
    series = list(
      list(
        id = "animals",
        data = dsan
      ),
      list(
        id = "fruits",
        data = dsfru
      ),
      list(
        id = "cars",
        data = dscar
      )
    )
  )


HTML widgets cannot be represented in plain text (need html)

In [34]:
df

name    y drilldown
1 Animals 5 animals  
2 Fruits  2 fruits   
3 Cars    4 cars

In [35]:
ndf

province_vector distances names                      value     demand   
1 1                4612.102 Province du Brabant wallon  89.25000  89.25000
5 5               29185.678 Province de Namur           92.18533  92.18533
2 2               49009.156 Province de Hainaut        274.61233 218.56467
3 3               85035.254 Province de Liège          172.70867   0.00000
4 4               98473.875 Province de Luxembourg       0.11900   0.00000

In [36]:
input_demand <- 200


cmap = brewer.pal(n = 11, name = 'Dark2')

datas = data.frame(X = c("Demand", "Remaining Offer"), Y = c(sum(ndf$demand), sum(ndf$value)-sum(ndf$demand)))

hchart(ndf,
    "pie", hcaes(x = names, y = value),
    name = "Offer", stack = "value", center = list("50%", "50%"))%>%#, borderColor = "#000000", borderWidth = 3 
    
hc_add_series(data = list(sum(ndf$demand), sum(ndf$value)-sum(ndf$demand)),
                    name=list("Demand"),type = "pie",
                    stack = "Values", colors = c('#FF0000', '#00ADFF2F'), 
                    dataLabels = list(enabled = FALSE), size = 200, borderColor = "white", borderWidth = 1,
              stack= "value", center = c("50%", "50%"), showInLegend = TRUE)%>%

hc_add_series(data = list(input_demand - sum(ndf$value), 3*sum(ndf$value)),
                    name=list("ecxess"),type = "pie",
                    stack = "Values", colors = c('#000000', '#00000000'), 
                    dataLabels = list(enabled = FALSE), size = 100, borderColor = "white", borderWidth = 1,
              stack= "value", center = c("50%", "50%"))

HTML widgets cannot be represented in plain text (need html)

# UI

In [90]:
cmap = brewer.pal(n = 11, name = 'Dark2')
ui  = dashboardPage(
    dashboardHeader(title = "Hello"),
    dashboardSidebar(
    sidebarMenu(
        menuItem("Dashboard", tabName = "dashboard", icon = icon("dashboard")),
        menuItem("Etat des lieux", tabName = "state", icon = icon("stats", lib = "glyphicon")),
        menuItem("About", tabName = "about", icon = icon("education", lib = "glyphicon"))

        )
    ),

    dashboardBody(
        tabItems(
            tabItem(tabName = "dashboard",
                fluidRow(
                    box(p("Choisissez le produit pour lequel vous voulez formuler une demande. \n 
                         Seule l'offre en produit frais sera impactée par la dimension temporelle."),
                        p("Une fois vos paramètres choisis, cliquez sur le bouton",strong(" \"Go!\""),
                          " tout en bas."),
                        title = ("Input parameters"), width = 5, solidHeader = TRUE,
                        status = "primary",
                        
                        sliderInput("input_demand", label = "Demande en Tonnes:", animate= FALSE,
                                    min = 0, max = 8000, step = 0.5, value = 50),
                        selectInput("input_time", label = "Mois:", choices =months),
                        selectInput("input_legume", label = "Legume:", choices =NULL),
                        numericInput("input_code", "Postal Code:", 1348, min = 1, max = 10000),
                        selectInput("input_production_mode", label = "Mode:", choices=NULL),
                        selectInput("input_transformation", label = "Transformation:",choices = NULL),
                        actionButton("goButton", strong("Go!")),
                        column(8, downloadButton("downloadwrodreport", "Download word report")))
                        ),

                    tabBox(
                        tabPanel(htmlOutput("bilantext"),
                              htmlOutput("locality"),
                              title = "Results", solidHeader = TRUE, status = "primary",
                              tableOutput("dat"),
                              htmlOutput("pietext"),
                              htmlOutput("pielegend"),  
                              
                              highchartOutput("pie")                  
                                ),
                        tabPanel(title = "Impacts", solidHeader = TRUE, status = "primary",
                                 tableOutput("impact")
                  
                                )
                            )
                        )
                    ,
                   
            tabItem(tabName = "about", h2("Bienvenue !"), box(
                   p("Cette application a été conçue par 5 étudiant bioingénieur de l'Uclouvain."),
                   p("Elle vous permet d'explorer les données que nous avons collectées au sujet de l'offre
                      en légumes de la wallonie et plus spécialement les",strong("Carottes, les Haricots, les Pois et les Oignons.")),
                   p("Dans le panel",strong("\"Dashboard\""), "vous pourrez formuler une demande et voir comment se répartierais l'offre
                      en fontion des provinces et de votre localité. Vous pourrez également vérifier si vous êtes dans la bonne
                      saison si vous voulez des produits frais, ou si vous êtes encore dans la période de conservation."),
                   p("Dans le panel",strong("\"Dashboard\""), "vous pourrez consulter les impacts environnementaux de votre
                      de votre demande et voir où elle se situe comparativement à la moyenne des différents modes de production disponibles.
                      Vous pourrez ainsi l'ajuster en fonction de vos priorités ou simplement comprendre à titre éducatif comment
                      les différents modes impact différement l'environnement."))),

            tabItem(tabName = "state",
                fluidRow(
                    box("Cliquez sur une province pour faire apparaitre son offre anuelle.",
                        title = "Click Me !", solidHeader = TRUE, width = 6, status = "primary",
                        leafletOutput("mymap")
                       ),
                    box("Cliquez sur un légume pour afficher sa production par mode.",
                        title = "Offre annuelle", solidHeader = TRUE, width = 6, status = "primary",
                    highchartOutput("mapplot")
                       )
                    )
                )
            )
        )
    )





# Server

In [91]:
second_el_to_numeric = function(ls){
  
  map(ls, function(x){
    x[[2]] = as.numeric(x[[2]])
    x
  })
  
}

server <- function(input, output, session) {
  
    ########################################
    # Set Inputs
    ########################################

    observe({
        updateSelectInput(session, "input_legume", choices = legumes$name)
    })

    
    observe({
        req(input$input_legume)
        id_leg <- legumes$id_legume[legumes$name == input$input_legume]
        id_modes <- unique(repartition_modes[repartition_modes$id_legume == id_leg,]$id_mode)
        names_modes <- production_modes$name[production_modes$id_mode %in% id_modes]

        updateSelectInput(session, "input_production_mode", choices = names_modes)
    })

    
    observe({
        req(input$input_legume)
        req(input$input_production_mode)
        id_leg <- legumes$id_legume[legumes$name == input$input_legume]
        id_modes <- production_modes$id_mode[production_modes$name == input$input_production_mode]
        id_transformation <- unique(repartition_modes$id_transformation[repartition_modes$id_legume == id_leg &                                                                      repartition_modes$id_mode == id_modes])
        name_transformation <- transformation$transformation[transformation$id_transformation %in% id_transformation]
        updateSelectInput(session, "input_transformation", choices = name_transformation)
    })
  
  
  
    ########################################
    # Dashboard & Impacts
    ########################################
 
    observeEvent(input$goButton,{            
            df = Main(input$input_demand, input$input_legume, input$input_code, input$input_time,
                      input$input_production_mode, input$input_transformation)
            locality = GetProvince(input$input_code)[[2]]
        
            output$dat = renderTable({table = df[[1]]})
            output$impact = renderTable({df[[2]]})
            output$locality = renderText({paste("Demande faite à ","<b>", locality[[1]], "</b>")})
            output$bilantext = renderText({paste("Voici votre bilan. Le programme commence par la province la plus proche devotre localisation puis, si l'offre n'est pas suffisante, explore lesautres provinces par ordre de proximité."
                                                )})
            })
        
    
                      
    
    ########################################
    # Pie
    ########################################
  
    
    observeEvent(
        input$goButton,{ndf = get_dispo(input$input_demand, input$input_legume, input$input_code,
        input$input_time, input$input_production_mode,
        input$input_transformation)
        demand = input$input_demand
        output$pietext = renderText({paste("Ce graphique représente la répartition de l\'offre par province.")})
        output$pielegend = renderText({paste(span(strong("En Rouge:"), style = "color:red", "Votre demande"),
                                             span(strong(" &#32 En Violet:"), style = "color:purple", "Votre excès"))})
        output$pie = renderHighchart({

            hchart(ndf,"pie", hcaes(x = names, y = value), name = "Offer",
                    center = list("300", "170"), size = 350)%>%
            
            hc_add_series(data = list(sum(ndf$demand), sum(ndf$value)-sum(ndf$demand)),
                    name=c("Demand"),type = "pie",
                    stack = "Values", colors = c('#FF0000', '#00ADFF2F'), 
                    dataLabels = list(enabled = FALSE), size = 180, center = c("300", "170"))%>%
            
            hc_add_series(data = list(demand - sum(ndf$value), 3*sum(ndf$value)),
                    name=list("Exces"),type = "pie",
                    stack = "Values", colors = c('#BA55D3', '#00000000'), 
                    dataLabels = list(enabled = FALSE), size = 80, borderColor = "white", borderWidth = 0,
                    stack= "value", center = c("300", "170"))

            })
        }
    )
                          
    ########################################
    # Map
    ########################################    
  
  
    output$mymap <- renderLeaflet({
        file = 'Database projet.xlsx'
        provinces = read_excel(file, sheet = 'provinces')
        file = 'code-postaux-belge.csv'
        df = read_csv2(file)
        
        lon1 = (df%>%filter(Code == input$input_code))$Longitude[[1]]
        lat1 = (df%>%filter(Code == input$input_code))$Latitude[[1]]
        localite = (df%>%filter(Code == input$input_code))$Localite

        icons <- icons("https://generations.fr/media/news/thumb/870x489_jujujul-65178.png",
                   iconWidth = 38, iconHeight = 25,
                   iconAnchorX = 0, iconAnchorY = 0,
                   shadowWidth = 50, shadowHeight = 64,
                   shadowAnchorX = 4, shadowAnchorY = 62)

        file = "BE_ADMIN_PROVINCE.rdata"
        load(file)

        poly_list = list()
        for(i in c(3,6,7,9,10)){poly_list = append(poly_list, BE_ADMIN_PROVINCE@polygons[[i]])}

        m <- leaflet(options = leafletOptions(zoomControl = FALSE, minZoom = 8, maxZoom = 8))%>%
            addProviderTiles("OpenStreetMap.Mapnik")%>%

            addPolygons(data = poly_list[[1]], fillColor = cmap[1],
                       color = 'black', opacity = 0.6, fillOpacity = 0.5,
                       highlight = highlightOptions(fillOpacity = 1, opacity = 1),label = "Brabant-Wallon",
                            labelOptions = labelOptions(
                                style = list("font-weight" = "normal", padding = "3px 8px"),
                                textsize = "15px",
                                direction = "auto"), layerId = 1)%>% 

            addPolygons(data = poly_list[[2]], fillColor = cmap[3],
                      color = 'black', opacity = 0.6, fillOpacity = 0.5,
                      highlight = highlightOptions(fillOpacity = 1, opacity = 1),label = "Hainaut",
                              labelOptions = labelOptions(
                                  style = list("font-weight" = "normal", padding = "3px 8px"),
                                  textsize = "15px",
                                  direction = "auto"), layerId = 2)%>% 

            addPolygons(data = poly_list[[3]], fillColor = cmap[6],
                      color = 'black', opacity = 0.6, fillOpacity = 0.5,
                      highlight = highlightOptions(fillOpacity = 1, opacity = 1), label = "Liège",
                            labelOptions = labelOptions(
                                style = list("font-weight" = "normal", padding = "3px 8px"),
                                textsize = "15px",
                                direction = "auto"), layerId = 3)%>% 

            addPolygons(data = poly_list[[4]], fillColor = cmap[8],
                      color = 'black', opacity = 0.6, fillOpacity = 0.5,
                      highlight = highlightOptions(fillOpacity = 1, opacity = 1), label = "Luxembourg",
                            labelOptions = labelOptions(
                                style = list("font-weight" = "normal", padding = "3px 8px"),
                                textsize = "15px",
                                direction = "auto"), layerId = 4)%>%

            addPolygons(data = poly_list[[5]], fillColor = cmap[5],
                      color = 'black', opacity = 0.6, fillOpacity = 0.5,
                      highlight = highlightOptions(fillOpacity = 1, opacity = 1), label = "Namur",
                            labelOptions = labelOptions(
                                style = list("font-weight" = "normal", padding = "3px 8px"),
                                textsize = "15px",
                                direction = "auto"), layerId = 5)%>%
        
            addMarkers(lon1, lat1, icon=icons, label=localite)


    })
   
  
    ########################################
    # Drilldown
    ########################################
    
    
    observe({ 
        event <- input$mymap_shape_click
        total_list = vector()
        if(is.null(event))
            return()
        else
            
            output$mapplot = renderHighchart({
            total_list = vector()
            pea_list = vector()
            bean_list = vector()
            carrot_list = vector()
            oinion_list = vector()
            for(input_legume in legumes$name){
                
                input_legume_id <- (legumes%>%filter(name == input_legume))$id_legume
                id_product_list = (repartition_modes%>%filter(id_legume == input_legume_id))$id_product
                yealds_id <- (impacts %>% filter(name == "Rendements"))$id_impact
                prod_list = vector()
                
                for(input_product_id in id_product_list){
                    
                    prod = get_production(input_product_id, event$id, yealds_id)
                    prod_list = append(prod_list, prod)
                }

                total = sum(prod_list)                
                total_list = append(total_list, total)
                
                if(input_legume == legumes$name[1]){pea_list = prod_list}
                if(input_legume == legumes$name[2]){bean_list = prod_list}
                if(input_legume == legumes$name[3]){carrot_list = prod_list}
                if(input_legume == legumes$name[4]){oinion_list = prod_list}
            }

            mod_list  = c("PC", "PRC", 'PO', 'FRC', 'FO', 'ZT')
            pea_df    = data.frame('name' = mod_list, 'value' = pea_list)
            pea_ds    = second_el_to_numeric(list_parse2(pea_df))
            bean_df   = data.frame('name' = mod_list, 'value' = bean_list)
            bean_ds   = second_el_to_numeric(list_parse2(bean_df))
            carrot_df = data.frame('name' = mod_list, 'value' = carrot_list)
            carrot_ds = second_el_to_numeric(list_parse2(carrot_df))
            onion_df  = data.frame('name' = mod_list, 'value' = oinion_list)
            onion_ds  = second_el_to_numeric(list_parse2(onion_df))


            map_df = data.frame(legumes$name, total_list)
            df <- data_frame(
                  name = c('Pea','Green beans','Carrot','Oinon'),
                  y = map_df$total_list,
                  drilldown = tolower(name))

            ds <- list_parse(df)
            names(ds) <- NULL
                
            hc <- highchart() %>%
                    hc_chart(type = "column")%>%
                
                    hc_title(text = paste("Total Offer in",
                                         (provinces%>%filter(id_province == event$id))$name))%>%
                
                    hc_xAxis(type = "category")%>%
                
                    hc_legend(enabled = FALSE)%>%
                
                    hc_plotOptions(
                        series = list(
                            boderWidth = 3, borderColor = "#000000",
                            dataLabels = list(enabled = FALSE)))%>%
                
                    hc_add_series(name="Legumes",
                                data = ds,
                                colorByPoint = TRUE,
                                borderColor = "#000000", borderWidth = 3)%>%
                
                    hc_drilldown(
                        allowPointDrilldown = TRUE,animation = list(duration = 1000),
                        series = list(
                        list(
                            id = 'pea',
                            data = pea_ds, borderColor = "#000000", borderWidth = 3),
                        list(
                            id = "green beans",
                            data = bean_ds,  borderColor = "#000000", borderWidth = 3),
                        list(
                            id = "carrot",
                            data = carrot_ds,  borderColor = "#000000", borderWidth = 3),
                        list(
                            id = "oinon",
                            data = onion_ds,  borderColor = "#000000", borderWidth = 3)
                                )
                      )
            })

    })
}


In [ ]:
shinyApp(ui = ui, server = server)


Listening on http://127.0.0.1:3545

Warning message:
“Unknown or uninitialised column: `id_legume`.”
Warning message:
“Error in : Must subset rows with a valid subscript vector.
ℹ Logical subscripts must match the size of the indexed input.
✖ Input has size 24 but subscript `repartition_modes$id_legume == id_leg` has size 0.”


In [44]:
file = 'Database projet.xlsx'
provinces = read_excel(file, sheet = 'provinces')
file = 'code-postaux-belge.csv'
df = read_csv2(file)
province_vector = vector()
distances = vector()
names = vector()
test = df%>%filter(Code == input_code)

if(length(test$Code) == 0){return(numeric(0))}

lon1 = (df%>%filter(Code == input_code))$Longitude[[1]]

lat1 = (df%>%filter(Code == input_code))$Latitude[[1]]
localite = (df%>%filter(Code == input_code))$Localite

icons <- icons("https://generations.fr/media/news/thumb/870x489_jujujul-65178.png",
  iconWidth = 38, iconHeight = 25,
  iconAnchorX = 0, iconAnchorY = 0,
  #shadowUrl = "http://leafletjs.com/examples/custom-icons/leaf-shadow.png",
  shadowWidth = 50, shadowHeight = 64,
  shadowAnchorX = 4, shadowAnchorY = 62
)


file = "BE_ADMIN_PROVINCE.rdata"
load(file)

poly_list = list()
for(i in c(3,6,7,9,10)){poly_list = append(poly_list, BE_ADMIN_PROVINCE@polygons[[i]])}

m <- leaflet(width=1000, height=1000) %>%
  addTiles()%>%
addPolygons(data = poly_list[[1]], fillColor = cmap[1],
            color = 'black', opacity = 0.6, fillOpacity = 0.5,
            highlight = highlightOptions(fillOpacity = 1, opacity = 1),label = "Brabant-Wallon",
            labelOptions = labelOptions(
            style = list("font-weight" = "normal", padding = "3px 8px"),
            textsize = "15px",
            direction = "auto"))%>% # BW

addPolygons(data = poly_list[[2]], fillColor = cmap[3],
            color = 'black', opacity = 0.6, fillOpacity = 0.5,
           highlight = highlightOptions(fillOpacity = 1, opacity = 1),label = "Hainaut",
            labelOptions = labelOptions(
            style = list("font-weight" = "normal", padding = "3px 8px"),
            textsize = "15px",
            direction = "auto"))%>% # Hainaut

addPolygons(data = poly_list[[3]], fillColor = cmap[6],
            color = 'black', opacity = 0.6, fillOpacity = 0.5,
           highlight = highlightOptions(fillOpacity = 1, opacity = 1), label = "Barakis",
            labelOptions = labelOptions(
            style = list("font-weight" = "normal", padding = "3px 8px"),
            textsize = "25px",
            direction = "auto"))%>% # Liege

addPolygons(data = poly_list[[4]], fillColor = cmap[8],
            color = 'black', opacity = 0.6, fillOpacity = 0.5,
           highlight = highlightOptions(fillOpacity = 1, opacity = 1), label = "Luxembourg",
            labelOptions = labelOptions(
            style = list("font-weight" = "normal", padding = "3px 8px"),
            textsize = "15px",
            direction = "auto"))%>% # Lux

addPolygons(data = poly_list[[5]], fillColor = cmap[5],
            color = 'black', opacity = 0.6, fillOpacity = 0.5,
            highlight = highlightOptions(fillOpacity = 1, opacity = 1), label = "Namur",
            labelOptions = labelOptions(
            style = list("font-weight" = "normal", padding = "3px 8px"),
            textsize = "15px",
            direction = "auto"))%>%
addMarkers(lon1, lat1, icon=icons, label=localite)
m



ℹ Using ',' as decimal and '.' as grouping mark. Use `read_delim()` for more control.



HTML widgets cannot be represented in plain text (need html)

In [ ]:
formattable(df[[1]],
                   list('status' = color_bar("lightblue"), orderable = true_false_formatter))


In [ ]:
true_false_formatter <-
  formatter("span",
            style = x ~ style(
              font.weight = "bold",
              color = ifelse(x == 1, "forestgreen", ifelse(x == FALSE, "red", "black"))
            ))

In [ ]:

id = 1

total_list = vector()
        pea_list = vector()
        bean_list = vector()
        carrot_list = vector()
        oinion_list = vector()
        for(input_legume in legumes$name){
          input_legume_id <- (legumes%>% 
                                filter(name == input_legume))$id_legume
          id_product_list = (repartition_modes%>%filter(id_legume == input_legume_id))$id_product
          yealds_id <- (impacts %>% 
                          filter(name == "Rendements"))$id_impact
          prod_list = vector()
          for(input_product_id in id_product_list){
            prod = get_production(input_product_id, id, yealds_id)
            prod_list = append(prod_list, prod)
            
          }
          
          total = sum(prod_list)
          
          total_list = append(total_list, total)
          if(input_legume == legumes$name[1]){pea_list = prod_list
                                              print(pea_list)}
          if(input_legume == legumes$name[2]){bean_list = prod_list
                                             print(bean_list)}
          if(input_legume == legumes$name[3]){carrot_list = prod_list
                                             print(carrot_list)}
          if(input_legume == legumes$name[4]){oinion_list = prod_list
                                             print(oinion_list)}
          
        }
        
        mod_list = c("PC", "PRC", 'PO', 'FRC', 'FO', 'ZT')
        pea_df = data.frame('name' = mod_list, 'value' = pea_list)
        pea_ds = second_el_to_numeric(list_parse2(pea_df))
        bean_df = data.frame('name' = mod_list, 'value' = bean_list)
        bean_ds = second_el_to_numeric(list_parse2(bean_df))
        carrot_df = data.frame('name' = mod_list, 'value' = carrot_list)
        carrot_ds = second_el_to_numeric(list_parse2(carrot_df))
        oinion_df = data.frame('name' = mod_list, 'value' = oinion_list)
        oinion_ds = second_el_to_numeric(list_parse2(oinion_df))
        
        
        map_df = data.frame(legumes$name, total_list)
        df <- data_frame(
          name = c('Pea','Green beans','Carrot','Oinon'),
          y = map_df$total_list,
          drilldown = tolower(name))
        
        ds <- list_parse(df)
        names(ds) <- NULL
        hc <- highchart() %>%
          hc_chart(type = "column") %>%
          hc_title(text = paste("Total Offer in",
                                (provinces%>%filter(id_province == id))$name)) %>%
          hc_xAxis(type = "category") %>%
          hc_legend(enabled = FALSE) %>%
          hc_plotOptions(
            series = list(
              boderWidth = 3, borderColor = "#000000",
              dataLabels = list(enabled = FALSE)))%>%
          hc_add_series(name="Legumes",
                        data = ds,
                        colorByPoint = TRUE,
                        borderColor = "#000000", borderWidth = 3)%>%
          hc_drilldown(
            allowPointDrilldown = TRUE,animation = list(duration = 1000),
            series = list(
              list(
                id = 'pea',
                data = pea_ds, borderColor = "#000000", borderWidth = 3
              ),
              list(
                id = "green beans",
                data = bean_ds,  borderColor = "#000000", borderWidth = 3
              ),
              list(
                id = "carrot",
                data = carrot_ds,  borderColor = "#000000", borderWidth = 3
              ),
              list(
                id = "oinon",
                data = oinion_ds,  borderColor = "#000000", borderWidth = 3
              )
            )
          )

In [ ]:
hc

In [ ]:
tdf = df[[2]]
formattable(tdf,
           align = c("l","c","r"))